In [13]:
import pandas as pd
import numpy as np
from sklearn import tree, metrics
from sklearn.preprocessing import StandardScaler
from sklearn.decomposition import PCA
from sklearn.pipeline import Pipeline
from sklearn.ensemble import RandomForestClassifier
from scipy.stats import mode
import math
import itertools

import os
import random

import pandas as pd
import numpy as np
from sklearn import tree, metrics
from sklearn.preprocessing import StandardScaler
from sklearn.decomposition import PCA
from sklearn.pipeline import Pipeline
from sklearn.ensemble import RandomForestClassifier
from scipy.stats import mode
import math
import itertools

import os

import GPyOpt
import numpy as np
import matplotlib.pyplot as plt
import torch
import numpy as np
from sklearn.metrics import roc_auc_score
from utils import plot_prototypes
from model import ShapeletGenerator, pairwise_dist
from mil import get_data
#from prototype_forest import PrototypeForest
import matplotlib.pyplot as plt
from pandas import DataFrame
import time
from os import listdir
from os.path import isfile, join
import os

In [57]:
import torch
import torch.nn as nn
import numpy as np


def gram_matrix(mat):
  mat = mat.squeeze(dim=0)
  mat = torch.mm(mat, mat.t())
  return mat



def pairwise_dist(x, y):
  x_norm = (x.norm(dim=2)[:, :, None])
  y_t = y.permute(0, 2, 1).contiguous()
  y_norm = (y.norm(dim=2)[:, None])
  y_t = torch.cat([y_t] * x.shape[0], dim=0)
  dist = x_norm + y_norm - 2.0 * torch.bmm(x, y_t)
  return torch.clamp(dist, 0.0, np.inf)

class ShapeletGenerator(nn.Module):

    def __init__(self, n_prototypes, bag_size, n_classes, features):
        n_prototypes = int(n_prototypes)
        super(ShapeletGenerator, self).__init__()

        number_of_rows = features.shape[0]

        random_indices = np.random.choice(number_of_rows, 
                                          size=1, 
                                         replace=False)
        
        prot = features[random_indices, :]
        print(features.shape)
        prot = prot.reshape(1, n_prototypes, prot.shape[1])
        prot = prot.astype("float32")
        self.prototypes = torch.from_numpy(prot).requires_grad_()
        #self.prototypes = (torch.randn(
        #    (1, n_prototypes, bag_size))).requires_grad_()
        if n_classes == 2:
            n_classes = 1
        self.linear_layer = torch.nn.Linear(3 * n_prototypes, n_classes, bias=False)
        #self.linear_layer.weight = torch.nn.Parameter(self.linear_layer.weight/100000)
        self.n_classes = n_classes

    def pairwise_distances(self, x, y):
        x_norm = (x.norm(dim=2)[:, :, None])
        y_t = y.permute(0, 2, 1).contiguous()
        y_norm = (y.norm(dim=2)[:, None])
        y_t = torch.cat([y_t] * x.shape[0], dim=0)
        dist = x_norm + y_norm - 2.0 * torch.bmm(x, y_t)
        return torch.clamp(dist, 0.0, np.inf)

    def get_output(self, batch_inp):
        dist = self.pairwise_distances(batch_inp, self.prototypes)
        min_dist = dist.min(dim=1)[0]
        max_dist = dist.max(dim=1)[0]
        mean_dist = dist.mean(dim=1)
        all_features = torch.cat([min_dist, max_dist, mean_dist], dim=1)
        logits = self.linear_layer(all_features)

        return logits, all_features

    def forward(self, x):
        logits, distances = self.get_output(x)
        if self.n_classes == 1:
          logits = logits.view(1)
        return logits, distances


def convert_to_bags(data,
                    split_instances=False,
                    instance_norm=True,
                    split_ratio=0.2,
                    stride_ratio=0.5):
  bags = []
  labels = []
  current_bag = []
  current_label = data[0, 0]
  cur = data[0, 1]
  instance_size = np.round(split_ratio * data[0, 2:].shape[0]).astype("int")
  stride = np.round(stride_ratio * instance_size).astype("int")

  for i in range(data.shape[0]):
    if data[i, 1] == cur:
      instance = data[i, 2:]
      if instance_norm:
        instance = (instance - np.mean(instance)) / (1e-08 + np.std(instance))
      if split_instances:
        size = instance.shape[0]
        window = instance_size
        while True:
          current_bag.append(instance[window - instance_size:window])
          window += stride
          if window >= size:
            window = size
            current_bag.append(instance[window - instance_size:window])
            break
      else:
        current_bag.append(instance)
    else:
      bags.append(np.array(current_bag))
      labels.append(np.array(current_label))
      current_label = data[i, 0]
      current_bag = []
      instance = data[i, 2:]
      if instance_norm:
        instance = (instance - np.mean(instance)) / (1e-08 + np.std(instance))
      if split_instances:
        size = instance.shape[0]
        window = instance_size
        while True:
          current_bag.append(instance[window - instance_size:window])
          window += stride
          if window >= size:
            window = size
            current_bag.append(instance[window - instance_size:window])
            break
      else:
        current_bag.append(instance)
      cur = data[i, 1]
  bags.append(np.array(current_bag))
  labels.append(np.array(current_label, dtype="int32"))
  return bags, labels

def find_prototype(bags,
                   features,
                   labels,
                   early_stopping_round = 10):
    
    n_classes=2
    n_epochs=100
    batch_size=1
    display_every=5
    final_vals = []
    reg_lambda_dist = generate_random(parameters[0][0], parameters[0][1])
    reg_lambda_w = generate_random(parameters[1][0], parameters[1][1])
    reg_lambda_p = generate_random(parameters[2][0], parameters[2][1])
    lr_prot = generate_random(parameters[3][0], parameters[3][1])
    lr_weights = generate_random(parameters[4][0], parameters[4][1])
    reg_w = 1
    n_prototypes = 1
    #reg_lambda_dist = 0.0005
    #reg_lambda_w = 0.005
    #reg_lambda_p = 0.00005
    #lr_prot = 0.00001
    #lr_weights = 0.00001
    #reg_w = 1
    #n_prototypes = 2
    #n_prototypes = n_prototypes*2
    
    data1 = np.vstack((labels, bags)).T
    data = np.concatenate([data1, features], axis=1)
    
    bags_train, labels_train = convert_to_bags(data)
    bags_train = np.array(bags_train)
    labels_train = np.array(labels_train)

    for rep in range(1, 2):
        vals = []
        for fold in range(1, 2):
            accs = [] 

            use_cuda = False

            bag_size = bags_train[0][0].shape[0]
            #step_per_epoch = len(bags_train)
            step_per_epoch = len(np.unique(bags))

            lr_step = (step_per_epoch * 40)
            display = (step_per_epoch * display_every)
            max_steps = n_epochs * step_per_epoch
            
            model = ShapeletGenerator(n_prototypes, bag_size, n_classes, features)

            if n_classes == 2:
                output_fn = torch.nn.Sigmoid()
            else:
                output_fn = torch.nn.Softmax()



            if n_classes == 2:
                loss = torch.nn.BCEWithLogitsLoss(reduction="mean")
            else:
                loss = torch.nn.CrossEntropyLoss(reduction="mean")

            optim1 = torch.optim.Adam([model.prototypes], lr=lr_prot)
            optim2 = torch.optim.Adam(list(model.linear_layer.parameters()),
                        lr=lr_weights)
            total_loss = 0
            correct = 0
            train_loss_hist, eval_loss_hist = [], []
            train_acc_hist, eval_acc_hist = [], []
            eval_aucs = []
            step_hist = []
            time_hist = []

            if use_cuda and torch.cuda.is_available():
                model = model.cuda()

            cont = True
            
            max_stagnation = 0 # number of epochs without improvement to tolerate
            best_prototype = None
            best_score = 0
            i = 0
            
            while i < max_steps and max_stagnation < early_stopping_round:
                i += 1
                np_idx = np.random.choice(bags_train.shape[0], batch_size)
                start_time = time.time()
                batch_inp = bags_train[np_idx]
                targets = torch.Tensor(labels_train[np_idx]).type(torch.int64)
                batch_inp = torch.Tensor(batch_inp[0])
                batch_inp = batch_inp.view(1, batch_inp.shape[0], batch_inp.shape[1])
                if use_cuda and torch.cuda.is_available():
                    targets = targets.cuda()
                    batch_inp = batch_inp.cuda()

                logits, distances = model(batch_inp)
                out = output_fn(logits)

                if n_classes == 2:
                    predicted = (out > 0.5).type(torch.int64)
                else:
                    _, predicted = torch.max(out, 1)
                correct += (predicted == targets).type(torch.float32).mean().item()

                batch_loss = loss(logits, targets.type(torch.float32))

                prototypes_pairwise = pairwise_dist(model.prototypes, model.prototypes)
                reg_prototypes = prototypes_pairwise.sum()

                weight_reg = 0
                for param in model.linear_layer.parameters():
                    weight_reg += param.norm(p=reg_w).sum()

                reg_loss = reg_lambda_w*weight_reg + reg_lambda_dist*distances.sum() - reg_prototypes*reg_lambda_p
                total_loss += batch_loss
                min_loss = batch_loss + reg_loss
                min_loss.backward()

                optim1.step()
                optim2.step()

                if (i + 1) % lr_step == 0:
                    print("LR DROP!")
                    optims = [optim1, optim2]
                    for o in optims:
                        for p in o.param_groups:
                            p["lr"] = p["lr"] / 2

                if (i + 1) % display == 0:
                    with torch.no_grad():
                        print("Step : ", str(i + 1), "Loss: ",
                        total_loss.item() / display, " accuracy: ", correct / (display))
                        train_loss_hist.append(total_loss.item() / display)
                        train_acc_hist.append(correct / display)
                        total_loss = 0
                        correct = 0
                        model = model.eval()
                        e_loss = 0
                        e_acc = 0
                        y_true = []
                        y_score = []

                        for i in range(len(bags_train)):
                            batch_inp = torch.Tensor(bags_train[i])
                            batch_inp = batch_inp.view(1, batch_inp.shape[0],
                                                  batch_inp.shape[1])
                            targets = torch.Tensor([labels_train[i]]).type(torch.int64)
                            logits, distances = model(batch_inp)
                            out = output_fn(logits)

                            if n_classes == 2:
                                predicted = (out > 0.5).type(torch.int64)
                            else:
                                _, predicted = torch.max(out, 1)
                            y_true.append(targets)
                            y_score.append(out)
                            correct = (predicted == targets).type(torch.float32).mean().item()
                            e_acc += correct
                            eval_loss = loss(logits, targets.type(torch.float32)).item()
                            e_loss += eval_loss

                        y_true_list = [x.tolist() for x in y_true]
                        y_score_list = [x.tolist() for x in y_score]
                        score_auc = roc_auc_score(y_true_list, y_score_list)
                        #print("Eval Loss: ", e_loss / len(bags_train),
                        #    " Eval Accuracy:", e_acc / len(bags_train), " AUC: ",
                        #score_auc)
                        
                        if score_auc > best_score:
                            best_score = score_auc
                            best_prototype = model.prototypes
                            max_stagnation = 0
                        else:
                            max_stagnation += 1
                        
                        #print("max_stagnation ", max_stagnation)
                        eval_loss_hist.append(e_loss / len(bags_train))
                        eval_acc_hist.append(e_acc / len(bags_train))
                        eval_aucs.append(roc_auc_score(y_true_list, y_score_list))
                        accs.append(e_acc / len(bags_train))
                        step_hist.append(i+1)
                        model = model.train()

    return best_prototype

In [58]:
class Node:
    def __init__(self):

        self.right = None
        self.left = None
        
        self.prototype = None
        
        self.column = None
        self.threshold = None
        
        self.probas = None
        self.depth = None
        
        self.is_terminal = False

In [59]:
class PrototypeTreeClassifier:
    def __init__(self,
                 train_features,
                 feature_types = ["min", "max", "mean"], 
                 max_depth = 3, 
                 min_samples_leaf = 1, 
                 min_samples_split = 2, 
                 prototype_count = 1,
                 use_prototype_learner=True,
                 early_stopping_round = 3):

        self.max_depth = max_depth
        self.min_samples_leaf = min_samples_leaf
        self.min_samples_split = min_samples_split
        self.prototype_count = prototype_count
        self.feature_types = feature_types
        self.train_features = train_features
        self.use_prototype_learner = use_prototype_learner
        self.Tree = None
        self.early_stopping_round = early_stopping_round
        
    def prototype(self, bags, features, labels, prototype_count):
        if self.use_prototype_learner:
            prototypes = find_prototype(bags, features, labels, self.early_stopping_round)
            check = prototypes.cpu().detach().numpy()

            check.resize(check.shape[1], check.shape[2])
            
            return check
        
        else:
            number_of_rows = self.train_features.shape[0]
            random_indices = np.random.choice(number_of_rows, 
                                              size=prototype_count, 
                                              replace=False)
            
            prot = self.train_features[random_indices, :]
            if len(prot.shape) == 1:
                prot = prot.reshape(1, prot.shape[0])
            return prot

    def nodeProbas(self, y):
        # for each unique label calculate the probability for it
        probas = []

        for one_class in self.classes:
            proba = y[y == one_class].shape[0] / y.shape[0]
            probas.append(proba)
        return np.asarray(probas)

    def features_via_prototype(self, feature_types, features, bag_ids, prototypes):
        distances = self.calculate_distances(features, prototypes)

        bin_count  = np.unique(bag_ids, return_counts=True)[1]
        ids, index  = np.unique(bag_ids, return_index=True)

        feature_list = []
        for i in range(0, prototypes.shape[0]):
            if "max" in feature_types:
                group_max = np.maximum.reduceat(distances[:, i], index)
                max_vals = np.repeat(group_max, bin_count)
                feature_list.append(max_vals)

            if "min" in feature_types:
                group_min = np.minimum.reduceat(distances[:, i], index)
                min_vals = np.repeat(group_min, bin_count)
                feature_list.append(min_vals)

            if "mean" in feature_types:
                group_sum = np.add.reduceat(distances[:, i], index)
                group_mean = np.add.reduceat(distances[:, i], index)
                mean_vals = np.repeat(group_mean, bin_count)
                feature_list.append(mean_vals)

        return np.array(np.transpose(feature_list))

    def dist1d(self, features, prototypes, distance_type="l2"):
        if distance_type == "l2":
            distance = np.linalg.norm(features - prototypes, axis=1)
        elif distance_type == "l1":
            distance = np.abs(features - prototypes)
            distance = np.sum(distance, axis=1)

        return distance

    def calculate_distances(self, features, prototypes):
        feature_list = []
        for i in range(0, prototypes.shape[0]):
            data = self.dist1d(features, prototypes[i], distance_type="l2")
            feature_list.append(data)
        data = np.column_stack(feature_list)

        return data

    def calcBestSplit(self, features, features_via_prototype, labels, bag_ids):
        bdc = tree.DecisionTreeClassifier(random_state=0, 
                                  max_depth=1, 
                                  criterion="entropy",
                                  min_samples_split=2)
        bdc.fit(features_via_prototype, labels.flatten())

        threshold = bdc.tree_.threshold[0]
        split_col = bdc.tree_.feature[0]

        features_left = features[features_via_prototype[:,split_col] <= bdc.tree_.threshold[0]]
        features_right = features[features_via_prototype[:,split_col] > bdc.tree_.threshold[0]]

        labels_left = labels[features_via_prototype[:,split_col] <= bdc.tree_.threshold[0]]
        labels_right = labels[features_via_prototype[:,split_col] > bdc.tree_.threshold[0]]

        bag_ids_left = bag_ids[features_via_prototype[:,split_col] <= bdc.tree_.threshold[0]]
        bag_ids_right = bag_ids[features_via_prototype[:,split_col] > bdc.tree_.threshold[0]]

        return split_col, threshold, features_left, features_right, labels_left, labels_right, bag_ids_left, bag_ids_right

    def buildDT(self, features, labels, bag_ids, node):
            '''
            Recursively builds decision tree from the top to bottom
            '''
            # checking for the terminal conditions

            if node.depth >= self.max_depth:
                node.is_terminal = True
                return

            if features.shape[0] < self.min_samples_split:
                node.is_terminal = True
                return

            if np.unique(labels).shape[0] == 1:
                node.is_terminal = True
                return

            node.prototype = self.prototype(bag_ids, features, labels, self.prototype_count)
            features_updated = self.features_via_prototype(self.feature_types, features, bag_ids, node.prototype)
            # calculating current split
            (splitCol, 
             thresh, 
             features_left, 
             features_right, 
             labels_left, 
             labels_right, 
             bag_ids_left, 
             bag_ids_right) = self.calcBestSplit(features, 
                                                 features_updated, 
                                                 labels, 
                                                 bag_ids)

            if splitCol is None:
                node.is_terminal = True
                return

            if features_left.shape[0] < self.min_samples_leaf or features_right.shape[0] < self.min_samples_leaf:
                node.is_terminal = True
                return

            node.column = splitCol
            node.threshold = thresh

            # creating left and right child nodes
            node.left = Node()
            node.left.depth = node.depth + 1
            node.left.probas = self.nodeProbas(labels_left)

            node.right = Node()
            node.right.depth = node.depth + 1
            node.right.probas = self.nodeProbas(labels_right)

            # splitting recursevely

            self.buildDT(features_right, labels_right, bag_ids_right, node.right)
            self.buildDT(features_left, labels_left, bag_ids_left, node.left)

    def fit(self, features, labels, bag_ids):
        '''
        Standard fit function to run all the model training
        '''
        self.classes = np.unique(labels)

        self.Tree = Node()
        self.Tree.depth = 1

        self.buildDT(features, labels, bag_ids, self.Tree)

    def predictSample(self, features, bag_ids, node):
        '''
        Passes one object through decision tree and return the probability of it to belong to each class
        '''

        # if we have reached the terminal node of the tree
        if node.is_terminal:
            return node.probas

        features_updated = self.features_via_prototype(self.feature_types, features, bag_ids, node.prototype)

        if features_updated[0][node.column] > node.threshold:
            probas = self.predictSample(features, bag_ids, node.right)
        else:
            probas = self.predictSample(features, bag_ids, node.left)

        return probas

    def predict(self, features, bag_ids):
        '''
        Returns the labels for each X
        '''

        if type(features) == pd.DataFrame:
            X = np.asarray(features)

        sort_index = np.argsort(bag_ids)
        bag_ids = bag_ids[sort_index]
        features = features[sort_index]

        features_updated = self.features_via_prototype(self.feature_types, features, bag_ids, self.Tree.prototype)

        index  = np.unique(bag_ids, return_index=True)[1]
        count  = np.unique(bag_ids, return_counts=True)[1]
        index = np.append(index, bag_ids.shape[0])   
        predictions = []

        for i in range(0, len(index) - 1):
            pred = np.argmax(self.predictSample(features[index[i]:index[i+1]], 
                                                bag_ids[index[i]:index[i+1]], 
                                                self.Tree))
            pred = np.repeat(pred, count[i])
            predictions = np.concatenate((predictions, pred), axis=0)

        return np.asarray(predictions)

In [60]:
def sample(features, labels, bag_ids, stratified, sample_rate):
    if stratified:
        pos_sample_size = math.ceil(np.where(labels == 1)[0].shape[0] * sample_rate)
        neg_sample_size = math.ceil(np.where(labels == 0)[0].shape[0] * sample_rate)
        indices_pos = np.random.choice(np.where(labels == 1)[0], pos_sample_size, replace=False)
        indices_neg = np.random.choice(np.where(labels == 0)[0], neg_sample_size, replace=False)
        inbag_indices = np.concatenate((indices_pos, indices_neg))
    else:
        sample_size = math.ceil(labels.shape[0] * sample_rate)
        inbag_indices = np.random.choice(np.where(labels == 1)[0], sample_size, replace=False)

    oo_bag_mask = np.ones(labels.shape[0], dtype=bool)
    oo_bag_mask[inbag_indices] = False

    outbag_indices = np.where(oo_bag_mask == 1)

    return inbag_indices, outbag_indices

def get_parameter_scores(features, labels, bag_ids, params, fit_on_full = True):
    keys, values = zip(*params.items())
    params_list = [dict(zip(keys, v)) for v in itertools.product(*values)]
    
    param_vals_scores = dict()
    for param_vals in params_list:
        if param_vals["explained_variance"] < 1:
            pipe = Pipeline([('pca', PCA(n_components = param_vals["explained_variance"], 
                             svd_solver = "full")), 
             ('scaler', StandardScaler()), ])
        else:
            pipe = Pipeline([('scaler', StandardScaler()), ])
        pipe.fit(features)

        train_features = pipe.transform(features)
        test_features = pipe.transform(features)

        score_list = []
        for i in range(0, param_vals["forest_size"]):
            (inbag_indices,
             outbag_indices) = sample(features, labels, bag_ids, stratified = True, sample_rate = 0.8)      

            inbag_features = features[inbag_indices]
            inbag_labels = labels[inbag_indices]
            inbag_bag_ids = bag_ids[inbag_indices]

            outbag_features = features[outbag_indices]
            outbag_labels = labels[outbag_indices]
            outbag_bag_ids = bag_ids[outbag_indices]

            model = PrototypeTreeClassifier(max_depth=param_vals["max_depth"], 
                                           min_samples_leaf=param_vals["min_samples_leaf"],
                                           min_samples_split=2)

            model.fit(inbag_features, inbag_labels, inbag_bag_ids)
            preds = model.predict(outbag_features, outbag_bag_ids)

            score = metrics.roc_auc_score(outbag_labels, preds)
            score_list.append(score)

        mean_score = sum(score_list)/len(score_list)
        key = frozenset(param_vals.items())
        param_vals_scores[key] = mean_score

    return param_vals_scores

In [61]:
def split_features_labels_bags(data):
    features = data[data.columns[~data.columns.isin([0, 1])]].to_numpy()
    labels = data[0].to_numpy()
    bag_ids = data[1].to_numpy()

    sort_index = np.argsort(bag_ids)
    bag_ids = bag_ids[sort_index]
    features = features[sort_index]
    
    return (features, labels, bag_ids)

def train_test_split(dataset, rep, fold, explained_variance, fit_on_full = False):
    data = pd.read_csv(f"/home/erdemb/Documents/data/{dataset}.csv", header=None)
    testbags =  pd.read_csv(f"/home/erdemb/Documents/libs/multi-instance-learning/cv/{dataset}.csv_rep{rep}_fold{fold}.txt", header=None)
    
    train_data = data[~data[1].isin(testbags[0].tolist())]    
    test_data = data[data[1].isin(testbags[0].tolist())]
    
    (train_features, train_labels, train_bag_ids) = split_features_labels_bags(train_data)
    (test_features, test_labels, test_bag_ids) = split_features_labels_bags(test_data)
    
    if explained_variance < 1:
        pipe = Pipeline([('pca', PCA(n_components = explained_variance, 
                         svd_solver = "full")), 
         ('scaler', StandardScaler()), ])
    else:
        pipe = Pipeline([('scaler', StandardScaler()), ])
    
    if fit_on_full:
        pipe.fit(data[data.columns[~data.columns.isin(['0','1'])]].to_numpy())
    else:
        pipe.fit(train_features)

    train_features = pipe.transform(train_features)
    test_features = pipe.transform(test_features)
    
    return (train_features, train_labels, train_bag_ids,
           test_features, test_labels, test_bag_ids)

In [62]:
params = {"min_samples_leaf": [2, 3], 
          "nof_prototypes": [2, 3], 
          "max_depth": [2, 3], 
          "forest_size": [10], 
          "explained_variance": [0.9, 0.95]}

In [63]:
class PrototypeForest:
    def __init__(self, size,
                feature_types = ["min", "mean", "max"],
                max_depth = 8, 
                min_samples_leaf = 2, 
                min_samples_split = 2, 
                prototype_count = 1,
                use_prototype_learner = True,
                early_stopping_round = 10):
        self.size = size
        self._trees = []
        self._tuning_trees = []
        self.max_depth = max_depth
        self.min_samples_leaf = min_samples_leaf
        self.min_samples_split = min_samples_split
        self.prototype_count = prototype_count
        self.use_prototype_learner = use_prototype_learner
        self.early_stopping_round = early_stopping_round
        
    def sample(self, features, labels, bag_ids):
        ids, index  = np.unique(bag_ids, return_index=True)
        group_min = np.minimum.reduceat(labels, index)
        pos_bag_size = math.ceil(np.where(group_min == 1)[0].shape[0] * 0.8)
        neg_bag_size = math.ceil(np.where(group_min == 0)[0].shape[0] * 0.8)
        bags_pos = np.random.choice(np.where(group_min == 1)[0], pos_bag_size, replace=False)
        bags_neg = np.random.choice(np.where(group_min == 0)[0], neg_bag_size, replace=False)
        df = pd.DataFrame(np.concatenate([train_bag_ids.reshape(train_bag_ids.shape[0],1),
                                          train_labels.reshape(train_labels.shape[0],1)],
                                         axis=1))
        indices_pos = df[df[0].isin(bags_pos)].index.to_numpy()
        indices_neg = df[df[0].isin(bags_neg)].index.to_numpy()
        inbag_indices = np.concatenate((indices_pos, indices_neg))
        oo_bag_mask = np.ones(labels.shape[0], dtype=bool)
        oo_bag_mask[inbag_indices] = False
        outbag_indices = np.where(oo_bag_mask == 1)
        
        return inbag_indices, outbag_indices
    
    def fit(self, features, labels, bag_ids):
        for i in range(self.size):
            if self.use_prototype_learner:
                print(f"Tree {i} will be trained")

            (inbag_indices,
             outbag_indices) = self.sample(features, labels, bag_ids)
            inbag_features = features[inbag_indices]
            inbag_labels = labels[inbag_indices]
            inbag_bag_ids = bag_ids[inbag_indices]
            tree = PrototypeTreeClassifier(
                max_depth=self.max_depth,
                min_samples_leaf=self.min_samples_leaf,
                min_samples_split=self.min_samples_split,
                prototype_count = self.prototype_count,
                use_prototype_learner = self.use_prototype_learner,
                train_features = inbag_features,
                early_stopping_round = self.early_stopping_round
            )
            tree.fit(inbag_features, inbag_labels, inbag_bag_ids)
            self._trees.append(tree)
            
    def predict(self, features, bag_ids):
        temp = [t.predict(features, bag_ids) for t in self._trees]
        preds = np.transpose(np.array(temp))
        return mode(preds,1)[0]
    
    def predict_proba(self, features, bag_ids):
        temp = [t.predict(features, bag_ids) for t in self._trees]
        preds = np.transpose(np.array(temp))
        return np.sum(preds==1, axis=1)/self.size

In [66]:
def generate_random(lower, upper):
    random_number = random.random()
    random_number = random_number + lower
    random_range = upper - lower
    random_number = random_number*random_range
    return random_number

dataset = "Musk2"

all_accuracy = []
parameters = [[0.00001, 0.05], [0.00001, 0.05],[0.00001, 0.05], [0.00001, 0.05], [0.00001, 0.05], [1],[1]]

for i in range(1,6):
    for j in range(1, 11):
        print(f"Rep {i}, fold {j}")
        (train_features,
             train_labels,
             train_bag_ids,
             test_features,
             test_labels,
             test_bag_ids) = train_test_split(dataset, i, j, 1, fit_on_full = False)
        
        model = PrototypeForest(size=100,
                                max_depth=8,
                                min_samples_leaf=40,
                                min_samples_split=80,
                                prototype_count=1,
                                early_stopping_round= 3,
                                use_prototype_learner = True)
        
        model.fit(train_features, train_labels, train_bag_ids)

        probas = model.predict_proba(test_features, test_bag_ids)

        score = metrics.roc_auc_score(test_labels, probas)
        print(f"Score is {score}")
        all_accuracy.append(metrics.roc_auc_score(test_labels, probas))

Fold 1, rep 1
Tree 0 will be trained
(291, 166)
Step :  285 Loss:  39.3164610745614  accuracy:  0.48771929824561405
Step :  285 Loss:  70.81196546052631  accuracy:  0.43508771929824563
Step :  285 Loss:  62.84954769736842  accuracy:  0.41754385964912283
Step :  285 Loss:  266.03678728070173  accuracy:  0.3894736842105263
(201, 166)
Step :  265 Loss:  36.01022626768868  accuracy:  0.5811320754716981
Step :  265 Loss:  21.05163251768868  accuracy:  0.47547169811320755
Step :  265 Loss:  18.520935288915094  accuracy:  0.5886792452830188
Step :  265 Loss:  124.93627653301887  accuracy:  0.5886792452830188
Step :  265 Loss:  128.5008991745283  accuracy:  0.5207547169811321
Step :  265 Loss:  21.02573334316038  accuracy:  0.5660377358490566
Step :  265 Loss:  52.05254274764151  accuracy:  0.4641509433962264
Step :  265 Loss:  110.65751031839622  accuracy:  0.5169811320754717
Step :  265 Loss:  169.9162883254717  accuracy:  0.5584905660377358
(151, 166)
Step :  175 Loss:  4.755495256696428  a

Step :  295 Loss:  1242.2495762711865  accuracy:  0.42033898305084744
Step :  295 Loss:  1584.3127118644068  accuracy:  0.43050847457627117
Step :  295 Loss:  2697.8080508474577  accuracy:  0.3728813559322034
Step :  295 Loss:  3560.755084745763  accuracy:  0.47796610169491527
Step :  295 Loss:  1994.8552966101695  accuracy:  0.4135593220338983
Step :  295 Loss:  1105.561652542373  accuracy:  0.43389830508474575
Step :  295 Loss:  4245.404661016949  accuracy:  0.36271186440677966
(218, 166)
Step :  280 Loss:  31.396498325892857  accuracy:  0.5321428571428571
Step :  280 Loss:  92.04226422991071  accuracy:  0.4785714285714286
Step :  280 Loss:  184.32745535714287  accuracy:  0.5821428571428572
Step :  280 Loss:  150.09086216517858  accuracy:  0.5071428571428571
Step :  280 Loss:  298.3955357142857  accuracy:  0.6178571428571429
Step :  280 Loss:  158.80559430803572  accuracy:  0.6214285714285714
Step :  280 Loss:  744.4395647321429  accuracy:  0.625
Step :  280 Loss:  256.35167410714286

Step :  295 Loss:  1260.5059322033899  accuracy:  0.36610169491525424
(199, 166)
Step :  260 Loss:  31.758946814903847  accuracy:  0.5115384615384615
Step :  260 Loss:  67.59169921875  accuracy:  0.49230769230769234
Step :  260 Loss:  235.92360276442307  accuracy:  0.3923076923076923
Step :  260 Loss:  261.42106370192306  accuracy:  0.4269230769230769
Step :  260 Loss:  404.28272235576924  accuracy:  0.38461538461538464
Tree 11 will be trained
(286, 166)
Step :  280 Loss:  101.03040597098214  accuracy:  0.5107142857142857
Step :  280 Loss:  273.5219866071429  accuracy:  0.3607142857142857
Step :  280 Loss:  288.2873604910714  accuracy:  0.43214285714285716
Step :  280 Loss:  274.12801339285716  accuracy:  0.4857142857142857
Step :  280 Loss:  1230.26328125  accuracy:  0.48928571428571427
Step :  280 Loss:  2127.509375  accuracy:  0.575
Step :  280 Loss:  1536.5815848214286  accuracy:  0.45714285714285713
Step :  280 Loss:  1918.8698660714285  accuracy:  0.48928571428571427
(196, 166)
S

Step :  185 Loss:  35.50745882601351  accuracy:  0.6324324324324324
Step :  185 Loss:  93.2761402027027  accuracy:  0.6702702702702703
Step :  185 Loss:  0.164856802450644  accuracy:  0.6324324324324324
(119, 166)
Step :  125 Loss:  24.75291015625  accuracy:  0.704
Step :  125 Loss:  20.159802734375  accuracy:  0.704
Step :  125 Loss:  3.605497314453125  accuracy:  0.68
Step :  125 Loss:  0.27171380615234375  accuracy:  0.664
Step :  125 Loss:  0.30498480224609376  accuracy:  0.696
Step :  125 Loss:  0.30498480224609376  accuracy:  0.688
Tree 17 will be trained
(291, 166)
Step :  285 Loss:  86.30097998903508  accuracy:  0.6
Step :  285 Loss:  118.56413103070176  accuracy:  0.543859649122807
Step :  285 Loss:  277.83684210526314  accuracy:  0.47017543859649125
Step :  285 Loss:  524.313596491228  accuracy:  0.4280701754385965
(210, 166)
Step :  270 Loss:  16.899620225694445  accuracy:  0.4962962962962963
Step :  270 Loss:  52.091059027777774  accuracy:  0.42962962962962964
Step :  270 L

Step :  300 Loss:  413.38994791666664  accuracy:  0.5666666666666667
Step :  300 Loss:  317.26359375  accuracy:  0.45666666666666667
(211, 166)
Step :  280 Loss:  100.58173130580357  accuracy:  0.5714285714285714
Step :  280 Loss:  175.23890904017858  accuracy:  0.6035714285714285
Step :  280 Loss:  146.97027064732143  accuracy:  0.5535714285714286
Step :  280 Loss:  357.2349609375  accuracy:  0.625
Step :  280 Loss:  558.7944754464286  accuracy:  0.5428571428571428
(115, 166)
Step :  120 Loss:  0.41895853678385414  accuracy:  0.49166666666666664
Step :  120 Loss:  0.27726020812988283  accuracy:  0.44166666666666665
Step :  120 Loss:  0.36422427495320636  accuracy:  0.3333333333333333
Step :  120 Loss:  0.38714364369710286  accuracy:  0.26666666666666666
(96, 166)
Step :  160 Loss:  3.3695350646972657  accuracy:  0.48125
Step :  160 Loss:  3.7772872924804686  accuracy:  0.5
Step :  160 Loss:  16.372496032714842  accuracy:  0.45625
Step :  160 Loss:  4.915151977539063  accuracy:  0.4562

...

Step :  165 Loss:  0.029406244104558773  accuracy:  0.7878787878787878
Step :  165 Loss:  27.683706202651514  accuracy:  0.8
Step :  165 Loss:  0.033607136119495735  accuracy:  0.806060606060606
Step :  165 Loss:  0.021004460074684837  accuracy:  0.806060606060606
Step :  165 Loss:  7.679989346590909  accuracy:  0.793939393939394
Tree 77 will be trained
(351, 166)
Step :  295 Loss:  77.9025622351695  accuracy:  0.4440677966101695
Step :  295 Loss:  299.98037605932205  accuracy:  0.36271186440677966
Step :  295 Loss:  259.2191472457627  accuracy:  0.39661016949152544
Step :  295 Loss:  412.6848781779661  accuracy:  0.4406779661016949
Step :  295 Loss:  247.72836334745762  accuracy:  0.3728813559322034
Step :  295 Loss:  483.5679555084746  accuracy:  0.4271186440677966
Step :  295 Loss:  619.6181144067797  accuracy:  0.4033898305084746
Step :  295 Loss:  1196.479025423729  accuracy:  0.37966101694915255
(209, 166)
Step :  235 Loss:  15.73724962599734  accuracy:  0.6425531914893617
Step :

Step :  310 Loss:  3.377312247983871  accuracy:  0.36451612903225805
Step :  310 Loss:  4.954798544606855  accuracy:  0.3903225806451613
Step :  310 Loss:  9.43703377016129  accuracy:  0.38387096774193546
(233, 166)
Step :  285 Loss:  29.573204495614036  accuracy:  0.5964912280701754
Step :  285 Loss:  33.99142680921052  accuracy:  0.5017543859649123
Step :  285 Loss:  61.76254797149123  accuracy:  0.4070175438596491
Step :  285 Loss:  31.728978207236842  accuracy:  0.6701754385964912
Step :  285 Loss:  46.6012266995614  accuracy:  0.6771929824561403
Step :  285 Loss:  19.72274191337719  accuracy:  0.47368421052631576
Step :  285 Loss:  68.43784265350877  accuracy:  0.6035087719298246
Step :  285 Loss:  53.65055167214912  accuracy:  0.6421052631578947
(121, 166)
Step :  185 Loss:  19.489113967483107  accuracy:  0.4918918918918919
Step :  185 Loss:  40.983688766891895  accuracy:  0.44324324324324327
Step :  185 Loss:  83.36775760135136  accuracy:  0.5243243243243243
Step :  185 Loss:  1

Step :  315 Loss:  1127.424107142857  accuracy:  0.37142857142857144
(219, 166)
Step :  270 Loss:  63.24970341435185  accuracy:  0.5740740740740741
Step :  270 Loss:  221.62758969907406  accuracy:  0.5518518518518518
Step :  270 Loss:  233.2355758101852  accuracy:  0.48518518518518516
Step :  270 Loss:  593.7607060185185  accuracy:  0.45555555555555555
Step :  270 Loss:  828.8904513888889  accuracy:  0.5333333333333333
Tree 88 will be trained
(346, 166)
Step :  300 Loss:  31.055491536458334  accuracy:  0.6133333333333333
Step :  300 Loss:  266.68015625  accuracy:  0.5066666666666667
Step :  300 Loss:  453.04182291666666  accuracy:  0.31666666666666665
Step :  300 Loss:  433.229921875  accuracy:  0.41
(217, 166)
Step :  275 Loss:  34.75451704545455  accuracy:  0.5381818181818182
Step :  275 Loss:  69.43036931818182  accuracy:  0.4618181818181818
Step :  275 Loss:  206.29646306818182  accuracy:  0.4763636363636364
Step :  275 Loss:  152.70421875  accuracy:  0.5818181818181818
Step :  275

Step :  140 Loss:  179.76212332589284  accuracy:  0.6214285714285714
Tree 95 will be trained
(345, 166)
Step :  295 Loss:  106.36539989406779  accuracy:  0.5084745762711864
Step :  295 Loss:  217.50805084745764  accuracy:  0.36610169491525424
Step :  295 Loss:  230.95617055084745  accuracy:  0.4610169491525424
Step :  295 Loss:  465.5625  accuracy:  0.511864406779661
Step :  295 Loss:  940.608686440678  accuracy:  0.43728813559322033
Step :  295 Loss:  1889.390466101695  accuracy:  0.5016949152542373
(165, 166)
Step :  75 Loss:  3.490526123046875  accuracy:  0.8266666666666667
Step :  75 Loss:  0.691205800374349  accuracy:  0.72
Step :  75 Loss:  0.1105816650390625  accuracy:  0.7866666666666666
Step :  75 Loss:  0.12014551798502604  accuracy:  0.7466666666666667
Step :  75 Loss:  0.11090354919433594  accuracy:  0.7733333333333333
(180, 166)
Step :  220 Loss:  55.78949307528409  accuracy:  0.5681818181818182
Step :  220 Loss:  11.937282492897728  accuracy:  0.5818181818181818
Step :  2

FileNotFoundError: [Errno 2] No such file or directory: '/home/erdemb/Documents/libs/multi-instance-learning/cv/Musk1.csv_rep6_fold1.txt'

In [69]:
np.mean(all_accuracy)/len(all_accuracy)

0.0185115426691653

In [75]:
dataset = "Musk1"

(train_features, 
     train_labels, 
     train_bag_ids,
     test_features, 
     test_labels, 
     test_bag_ids) = train_test_split(dataset, 1, 1, 1, fit_on_full = False)

for i in range(0, 2):
    model = PrototypeForest(
        size = 100, 
        max_depth = 8, 
        min_samples_leaf= 40, 
        min_samples_split= 80, 
        feature_types=["min", "max", "mean"]
    )
    model.fit(train_features, train_labels, train_bag_ids)
    preds = model.predict(test_features, test_bag_ids)
    probas = model.predict_proba(test_features, test_bag_ids)
    print(metrics.roc_auc_score(test_labels, probas))
    print(metrics.accuracy_score(test_labels, preds))

0.9351851851851852
0.8095238095238095
0.9097222222222222
0.6428571428571429


In [26]:
rep = 5
nofCVfold = 10
dataset = "BrownCreeper"
accuracy = []

#param_scores = get_parameter_scores(train_features, train_labels, train_bag_ids, params)
#best_params = dict(max(param_scores, key=param_scores.get))

for rep in range(1, 2):
    for fold in range(1, 11):
        (train_features, 
         train_labels, 
         train_bag_ids,
         test_features, 
         test_labels, 
         test_bag_ids) = train_test_split(dataset, 
                                          rep, 
                                          fold, 
                                          best_params["explained_variance"], 
                                          fit_on_full = False)
        
        model = PrototypeForest(size = 15, 
                                max_depth = best_params["max_depth"], 
                                min_samples_leaf=best_params["min_samples_leaf"], 
                                min_samples_split=2,
                                prototype_count=best_params["nof_prototypes"])
        
        model.fit(train_features, train_labels, train_bag_ids)
        preds = model.predict(test_features, test_bag_ids)
        accuracy.append(metrics.accuracy_score(test_labels, preds))

NameError: name 'best_params' is not defined

In [30]:
rep = 5
nofCVfold = 10
dataset = "BrownCreeper"
accuracy = []

#param_scores = get_parameter_scores(train_features, train_labels, train_bag_ids, params)
#best_params = dict(max(param_scores, key=param_scores.get))

for rep in range(1, 2):
    for fold in range(1, 11):
        (train_features, 
         train_labels, 
         train_bag_ids,
         test_features, 
         test_labels, 
         test_bag_ids) = train_test_split(dataset, 
                                          rep, 
                                          fold, 
                                          1, 
                                          fit_on_full = False)
        
        model = PrototypeForest(size = 100, 
                                max_depth = 3, 
                                min_samples_leaf=3, 
                                min_samples_split=2,
                                prototype_count=3)
        
        model.fit(train_features, train_labels, train_bag_ids)
        preds = model.predict(test_features, test_bag_ids)
        accuracy.append(metrics.accuracy_score(test_labels, preds))

In [31]:
np.mean(accuracy)

0.8384378229864422

In [ ]:
bdc = tree.DecisionTreeClassifier(random_state=0, 
                                  max_depth=2, 
                                  criterion="entropy",
                                  min_samples_split=2)

bdc.fit(features, labels)
for i in range(0, 5):
    bdc.fit(train_features, train_labels)
    predictions = bdc.predict(test_features)
    print(metrics.accuracy_score(test_labels, predictions))

In [151]:
for i in range(0, 1):
    bdc = RandomForestClassifier(n_estimators=15,
                                 random_state=0, 
                                 max_depth=2, 
                                 criterion="entropy",
                                 min_samples_split=2)
    bdc.fit(train_features, train_labels)
    preds = bdc.predict_proba(test_features)
    print(metrics.roc_auc_score(test_labels, preds[:, 1]))

0.674985538729156


In [24]:
bdc = RandomForestClassifier(n_estimators=15,
                             random_state=0, 
                             max_depth=2, 
                             criterion="entropy",
                             min_samples_split=2)
accuracy = []

for rep in range(1, 2):
    for fold in range(1, 11):
        (train_features, 
         train_labels, 
         train_bag_ids,
         test_features, 
         test_labels, 
         test_bag_ids) = train_test_split(dataset, rep, fold, 0.95, fit_on_full = False)
        
        bdc.fit(train_features, train_labels)
        predictions = bdc.predict(test_features)
        accuracy.append(metrics.accuracy_score(test_labels, predictions))

In [75]:
print(pd.__version__)
print(sklearn.__version__)

1.2.3
0.24.1
